# Statistical Baselines

In [4]:
import pandas as pd
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import f1_score
from sklearn.model_selection import GridSearchCV
from sklearn.naive_bayes import ComplementNB
from sklearn.svm import LinearSVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.dummy import DummyClassifier

In [5]:
test_df = pd.read_csv("../../data/prepared/test.csv")
train_df = pd.read_csv("../../data/prepared/train.csv")
valid_df = pd.read_csv("../../data/prepared/valid.csv")
unlabeled_df = pd.read_csv("../../data/prepared/unlabeled.csv")
bigger_train_df = pd.concat([train_df, valid_df], ignore_index=True)
results = {}

## Most Common and Stratified Baselines

In [6]:
baseline_classifier = DummyClassifier(strategy='most_frequent', random_state=42)
baseline_classifier.fit(train_df["problem_abstract"], train_df["team"])
y_pred = baseline_classifier.predict(test_df["problem_abstract"])
results["dummy most common"] = f1_score(test_df["team"], y_pred, average='micro')
print("F1-micro Score on Test Set:", results["dummy most common"])

baseline_classifier = DummyClassifier(strategy='stratified', random_state=42)
baseline_classifier.fit(train_df["problem_abstract"], train_df["team"])
y_pred = baseline_classifier.predict(test_df["problem_abstract"])
results["dummy stratified"] = f1_score(test_df["team"], y_pred, average='micro')
print("F1-micro Score on Test Set:", results["dummy stratified"])

F1-micro Score on Test Set: 0.3333333333333333
F1-micro Score on Test Set: 0.18984547461368653


## Log Regression

In [7]:
# Fit tfidf transformer on unlabeled and train data
train_unlabeled_df = pd.concat([train_df, unlabeled_df], ignore_index=True)
tfidf = TfidfVectorizer().fit(train_unlabeled_df['problem_abstract'].apply(lambda s: "" if s is None or pd.isna(s) else s))

# Transform train and test data
X_train = tfidf.transform(train_df["problem_abstract"].apply(lambda s: "" if s is None or pd.isna(s) else s))
y_train = train_df['team']
X_test = tfidf.transform(test_df['problem_abstract'].apply(lambda s: "" if s is None or pd.isna(s) else s))
y_test = test_df['team']

In [8]:
def finetune(X_train, y_train, model, param_grid, metric, cv=5, verbose=2):

    grid_search = GridSearchCV(model, param_grid, cv=5, scoring=metric, verbose=verbose)
    grid_search.fit(X_train, y_train)
    best_model = grid_search.best_estimator_
    best_params = grid_search.best_params_
    return best_model, best_params

def evaluate(X_test, y_test, model):

    y_pred = model.predict(X_test)
    metric = f1_score(y_test, y_pred, average="micro")
    return metric

model, model_params = finetune(
    X_train, 
    y_train,
    LogisticRegression(random_state=42, penalty="elasticnet", class_weight="balanced", n_jobs=-1, solver="saga"),
    {
        "C": [0.01, 0.1, 1.0, 10.0],
        "l1_ratio": [0.0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0]
    },
    "f1_micro",
    cv=5,
    verbose=2
    )
print("Best Hyperparameters:", model_params)
results["logistic regression"] = evaluate(X_test, y_test, model)
print("F1-micro Score on Test Set:", results["logistic regression"])

Fitting 5 folds for each of 44 candidates, totalling 220 fits


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   3.8s
[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   3.7s
[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   3.5s
[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   3.8s
[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   4.0s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   3.6s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   3.8s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   4.0s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   3.9s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   3.7s
[CV] END ...............................C=0.01, l1_ratio=0.2; total time=   3.7s
[CV] END ...............................C=0.01, l1_ratio=0.2; total time=   4.0s
[CV] END ...................

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ................................C=0.1, l1_ratio=0.0; total time=   5.7s


...

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ...............................C=10.0, l1_ratio=1.0; total time=   6.6s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ...............................C=10.0, l1_ratio=1.0; total time=   6.7s
Best Hyperparameters: {'C': 10.0, 'l1_ratio': 0.6}
F1-micro Score on Test Set: 0.5629139072847682


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


## Naive Bayes

In [9]:
model, model_params = finetune(
    X_train, 
    y_train,
    ComplementNB(),
    {
        "norm": [True, False],
        "alpha": [0.0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0],
        
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["naive bayes"] = evaluate(X_test, y_test, model)
print("F1-micro Score on Test Set:", results["naive bayes"])

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:624: FutureWarning: The default value for `force_alpha` will change to `True` in 1.4. To suppress this warning, manually set the value of `force_alpha`.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:633: UserWarning: alpha too small will result in numeric errors, setting alpha = 1.0e-10. Use `force_alpha=True` to keep alpha unchanged.
  warnings.warn(


Fitting 5 folds for each of 22 candidates, totalling 110 fits
[CV] END ...............................alpha=0.0, norm=True; total time=   0.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:624: FutureWarning: The default value for `force_alpha` will change to `True` in 1.4. To suppress this warning, manually set the value of `force_alpha`.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:633: UserWarning: alpha too small will result in numeric errors, setting alpha = 1.0e-10. Use `force_alpha=True` to keep alpha unchanged.
  warnings.warn(


[CV] END ...............................alpha=0.0, norm=True; total time=   0.1s
[CV] END ...............................alpha=0.0, norm=True; total time=   0.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:624: FutureWarning: The default value for `force_alpha` will change to `True` in 1.4. To suppress this warning, manually set the value of `force_alpha`.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:633: UserWarning: alpha too small will result in numeric errors, setting alpha = 1.0e-10. Use `force_alpha=True` to keep alpha unchanged.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:624: FutureWarning: The default value for `force_alpha` will change to `True` in 1.4. To suppress this warning, manually set the value of `force_alpha`.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_ba

[CV] END ...............................alpha=0.0, norm=True; total time=   0.1s
[CV] END ...............................alpha=0.0, norm=True; total time=   0.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:624: FutureWarning: The default value for `force_alpha` will change to `True` in 1.4. To suppress this warning, manually set the value of `force_alpha`.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:633: UserWarning: alpha too small will result in numeric errors, setting alpha = 1.0e-10. Use `force_alpha=True` to keep alpha unchanged.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:624: FutureWarning: The default value for `force_alpha` will change to `True` in 1.4. To suppress this warning, manually set the value of `force_alpha`.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_ba

[CV] END ..............................alpha=0.0, norm=False; total time=   0.2s
[CV] END ..............................alpha=0.0, norm=False; total time=   0.1s
[CV] END ..............................alpha=0.0, norm=False; total time=   0.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:624: FutureWarning: The default value for `force_alpha` will change to `True` in 1.4. To suppress this warning, manually set the value of `force_alpha`.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:633: UserWarning: alpha too small will result in numeric errors, setting alpha = 1.0e-10. Use `force_alpha=True` to keep alpha unchanged.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py:624: FutureWarning: The default value for `force_alpha` will change to `True` in 1.4. To suppress this warning, manually set the value of `force_alpha`.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_ba

[CV] END ..............................alpha=0.0, norm=False; total time=   0.1s
[CV] END ..............................alpha=0.0, norm=False; total time=   0.1s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.1s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.1s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.1s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.1s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.1s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.1s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.1s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.1s
[CV] END ...................

## Linear SVM

In [10]:
model, model_params = finetune(
    X_train, 
    y_train,
    LinearSVC(loss="squared_hinge", class_weight="balanced", random_state=42),
    {
        "penalty": ["l1", "l2"],
        "C": [0.001, 0.01, 0.1, 1.0, 10.0, 100],
        "intercept_scaling": [0.001, 0.01, 0.1, 1.0, 10.0, 100]
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["linear svm"] = evaluate(X_test, y_test, model)
print("F1-micro Score on Test Set:", results["linear svm"])

Fitting 5 folds for each of 72 candidates, totalling 360 fits
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: Th

[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.1s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.1s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(


[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.1s
[CV] END ........C=0.001, intercept_scaling=0.01, penalty=l1; total time=   0.0s
[CV] END ........C=0.001, intercept_scaling=0.01, penalty=l1; total time=   0.0s
[CV] END ........C=0.001, intercept_scaling=0.01, penalty=l1; total time=   0.0s
[CV] END ........C=0.001, intercept_scaling=0.01, penalty=l1; total time=   0.0s
[CV] END ........C=0.001, intercept_scaling=0.01, penalty=l1; total time=   0.0s
[CV] END ........C=0.001, intercept_scaling=0.01, penalty=l2; total time=   0.1s
[CV] END ........C=0.001, intercept_scaling=0.01, penalty=l2; total time=   0.1s


...

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(


[CV] END ...........C=100, intercept_scaling=100, penalty=l2; total time=   7.4s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:425: FitFailedWarning: 
180 fits failed out of a total of 360.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
180 fits failed with the following error:
Traceback (most recent call last):
  File "/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score

[CV] END ...........C=100, intercept_scaling=100, penalty=l2; total time=   7.6s
Best Hyperparameters: {'C': 10.0, 'intercept_scaling': 10.0, 'penalty': 'l2'}
F1-micro Score on Test Set: 0.7362030905077263


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


## Random Forest

In [11]:
model, model_params = finetune(
    X_train, 
    y_train,
    RandomForestClassifier(class_weight="balanced", random_state=42, n_jobs=-1),
    {
        "min_samples_split": [2, 4, 6, 8, 10, 12, 14, 16, 18, 20],
        "min_samples_leaf": [2, 4, 6, 8, 10, 12, 14, 16, 18, 20],
        "max_samples": [0.6, 0.7, 0.8, 0.9, 1.0]
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["random forest"] = evaluate(X_test, y_test, model)
print("F1-micro Score on Test Set:", results["random forest"])

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


Fitting 5 folds for each of 500 candidates, totalling 2500 fits
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   1.1s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.9s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   1.0s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   1.0s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   1.0s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.9s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.9s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   1.0s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.9s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   1.0s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=6; total tim

## Evaluation

In [12]:
pd.DataFrame.from_dict(results, orient="index", columns=["f1 micro"])

f1 micro
dummy most common    0.333333
dummy stratified     0.189845
logistic regression  0.562914
naive bayes          0.753863
linear svm           0.736203
random forest        0.567329
Bert                 0.000000